<a href="https://colab.research.google.com/github/PriyankaDataAnalyst/Music_recommendation/blob/main/MusicRecommendation2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import requests
import base64

# Replace with your own Client ID and Client Secret
CLIENT_ID = '19b2842465bb4232a2d2759769f103fc'
CLIENT_SECRET = '5fd6afc2c142472690b3abbd08b20a7d'

# Base64 encode the client ID and client secret
client_credentials = f"{CLIENT_ID}:{CLIENT_SECRET}"
client_credentials_base64 = base64.b64encode(client_credentials.encode())

# Request the access token
token_url = 'https://accounts.spotify.com/api/token'
headers = {
    'Authorization': f'Basic {client_credentials_base64.decode()}'
}
data = {
    'grant_type': 'client_credentials'
}
response = requests.post(token_url, data=data, headers=headers)

if response.status_code == 200:
    access_token = response.json()['access_token']
    print("Access token obtained successfully.")
else:
    print("Error obtaining access token.")
    exit()

Access token obtained successfully.


In [ ]:
pip install spotipy


In [ ]:
import pandas as pd
import spotipy
from spotipy.oauth2 import SpotifyOAuth

def get_trending_playlist_data(playlist_id, access_token, limit=100):
    # Set up Spotipy with the access token
    sp = spotipy.Spotify(auth=access_token)

    # Initialize list to store music data
    music_data = []

    # Initialize offset for pagination
    offset = 0

    # Loop to retrieve all tracks from the playlist
    while True:
        # Get the tracks from the playlist with pagination
        playlist_tracks = sp.playlist_tracks(playlist_id, fields='items(track(id, name, artists, album(id, name)))', limit=limit, offset=offset)

        # If no more tracks are available, break the loop
        if not playlist_tracks['items']:
            break

        # Extract relevant information and store in a list of dictionaries
        for track_info in playlist_tracks['items']:
            track = track_info['track']
            track_name = track['name']
            artists = ', '.join([artist['name'] for artist in track['artists']])
            album_name = track['album']['name']
            album_id = track['album']['id']
            track_id = track['id']

            # Get audio features for the track
            audio_features = sp.audio_features(track_id)[0] if track_id != 'Not available' else None

            # Get release date of the album
            try:
                album_info = sp.album(album_id) if album_id != 'Not available' else None
                release_date = album_info['release_date'] if album_info else None
            except:
                release_date = None

            # Get popularity of the track
            try:
                track_info = sp.track(track_id) if track_id != 'Not available' else None
                popularity = track_info['popularity'] if track_info else None
            except:
                popularity = None

            # Add additional track information to the track data
            track_data = {
                'Track Name': track_name,
                'Artists': artists,
                'Album Name': album_name,
                'Album ID': album_id,
                'Track ID': track_id,
                'Popularity': popularity,
                'Release Date': release_date,
                'Duration (ms)': audio_features['duration_ms'] if audio_features else None,
                'Explicit': track_info.get('explicit', None),
                'External URLs': track_info.get('external_urls', {}).get('spotify', None),
                'Danceability': audio_features['danceability'] if audio_features else None,
                'Energy': audio_features['energy'] if audio_features else None,
                'Key': audio_features['key'] if audio_features else None,
                'Loudness': audio_features['loudness'] if audio_features else None,
                'Mode': audio_features['mode'] if audio_features else None,
                'Speechiness': audio_features['speechiness'] if audio_features else None,
                'Acousticness': audio_features['acousticness'] if audio_features else None,
                'Instrumentalness': audio_features['instrumentalness'] if audio_features else None,
                'Liveness': audio_features['liveness'] if audio_features else None,
                'Valence': audio_features['valence'] if audio_features else None,
                'Tempo': audio_features['tempo'] if audio_features else None,
                # Add more attributes as needed
            }

            music_data.append(track_data)

        # Increment offset for next pagination request
        offset += limit

    # Create a pandas DataFrame from the list of dictionaries
    df = pd.DataFrame(music_data)

    return df


In [ ]:
playlist_id = '3ETY4ZSSqwB0r8EoKZfml4'

# Call the function to get the music data from the playlist and store it in a DataFrame
music_df = get_trending_playlist_data(playlist_id, access_token)

# Display the DataFrame
print(music_df)

ERROR:spotipy.client:Max Retries reached


SpotifyException: http status: 429, code:-1 - /v1/audio-features/?ids=1px3n4J5oTV4XiSoyEYvLA:
 Max Retries, reason: too many 429 error responses

In [ ]:
print(music_df.isnull().sum())

Track Name          0
Artists             0
Album Name          0
Album ID            0
Track ID            0
Popularity          0
Release Date        0
Duration (ms)       0
Explicit            0
External URLs       0
Danceability        0
Energy              0
Key                 0
Loudness            0
Mode                0
Speechiness         0
Acousticness        0
Instrumentalness    0
Liveness            0
Valence             0
Tempo               0
dtype: int64


In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from datetime import datetime
from sklearn.metrics.pairwise import cosine_similarity

music_df

Track Name  \
0                      Yaaro Ivan (From "Udhayam NH4")   
1           Ae Le Le Etti Paarthale - From "Naiyaandi"   
2                              Vizhigalil Oru Vaanavil   
3                                      Yedhedho Pennae   
4                                          Kan Irandil   
5                                        Sotta Sotta m   
6                                          Kattu Kattu   
7                                       Kaadhal Endral   
8                                              Pogadhe   
9                             Idhayam (From "Billa 2")   
10                                        Iragai Poley   
11                                   Yedho Ondru Ennai   
12                                      Manmadhane Nee   
13                Aathadi Manasudhan (From "Kazhugoo")   
14                                          Oru Naalil   
15                                             Oh Baby   
16                                     En Kadhal Solla   
17                                  Evan Di Una Pethan   
18                                         Nallamdhana   
19                                        Nahna Na Nah   
20                            Mutham Kodutha Maayakari   
21                                       Vallava Ennai   
22                                        High On Love   
23                                            Neethane   
24                                      Kaadhal Vaithu   
25                                        Kannai Vittu   
26                                           Siragugal   
27                                Theeratha Vilaiyattu   
28                              Andha Kanna Paathaakaa   
29                                          Top Tucker   
30         Per Vachaalum Vaikkaama (From "Dikkiloona")   
31                                      Kambathu Ponnu   
32                                 Wake Me up Everyday   
33                    Thattiputta - From "Maamanithan"   
34                                        Kanave Urave   
35                                     Adi Yendi Pulla   
36                                         Thuli Thuli   
37                                    En Jannal Vandha   
38                                        Oru Devathai   
39                                   Saayndhu Saayndhu   
40                                   Chinna Chinnathai   
41                                      Enkeyoo Partha   
42                                              Vaanam   
43                                                 Goa   
44                             Trend Song (From "Aaa")   
45                                   All Day Jolly Day   
46                                            Hey Sala   
47                                      Adada Mazhaida   
48                                        Kaatrukullai   
49                      Oru Kan Jaadai (From "Anjaan")   
50                                            Venmegam   
51                                      Pengal Yendral   
52                               Seermevum Koovathiley   
53                                 Idhayathai Oru Nodi   
54                                    Lets Be Friends?   
55                                      Ammadi Aathadi   
56                                   Unnai Unnai Unnai   
57                 Lovvu Lovvu - From "Anbulla Ghilli'   
58                  Over'a Feel Pannuren (From "Hero")   
59                      Malto Kithapuleh (From "Hero")   
60                           Title Track (From "Hero")   
61                                 Poongatre Poongatre   
62                                   Oh Shala Oh Shala   
63                                      Nenjai Kasakki   
64                                      Pachchai Vanna   
65                                   Suthudhe Suthudhe   
66                                  Kannan Varum Velai   
67                                    Kadal Raasa Naan   
68                                       E

In [ ]:
# Assuming 'df' is your DataFrame containing the dataset
# Specify the positional indices of the rows you want to delete
indices_to_delete = [71,99]  # Replace [2, 5] with the actual positional indices of the rows you want to delete

# Delete the rows with the specified positional indices
music_df.drop(music_df.index[indices_to_delete], inplace=True)

pd.set_option('display.max_rows', None)

# Assuming 'df' is your DataFrame containing the dataset
# Display the entire DataFrame
display(music_df)

Track Name  \
0                      Yaaro Ivan (From "Udhayam NH4")   
1           Ae Le Le Etti Paarthale - From "Naiyaandi"   
2                              Vizhigalil Oru Vaanavil   
3                                      Yedhedho Pennae   
4                                          Kan Irandil   
5                                        Sotta Sotta m   
6                                          Kattu Kattu   
7                                       Kaadhal Endral   
8                                              Pogadhe   
9                             Idhayam (From "Billa 2")   
10                                        Iragai Poley   
11                                   Yedho Ondru Ennai   
12                                      Manmadhane Nee   
13                Aathadi Manasudhan (From "Kazhugoo")   
14                                          Oru Naalil   
15                                             Oh Baby   
16                                     En Kadhal Solla   
17                                  Evan Di Una Pethan   
18                                         Nallamdhana   
19                                        Nahna Na Nah   
20                            Mutham Kodutha Maayakari   
21                                       Vallava Ennai   
22                                        High On Love   
23                                            Neethane   
24                                      Kaadhal Vaithu   
25                                        Kannai Vittu   
26                                           Siragugal   
27                                Theeratha Vilaiyattu   
28                              Andha Kanna Paathaakaa   
29                                          Top Tucker   
30         Per Vachaalum Vaikkaama (From "Dikkiloona")   
31                                      Kambathu Ponnu   
32                                 Wake Me up Everyday   
33                    Thattiputta - From "Maamanithan"   
34                                        Kanave Urave   
35                                     Adi Yendi Pulla   
36                                         Thuli Thuli   
37                                    En Jannal Vandha   
38                                        Oru Devathai   
39                                   Saayndhu Saayndhu   
40                                   Chinna Chinnathai   
41                                      Enkeyoo Partha   
42                                              Vaanam   
43                                                 Goa   
44                             Trend Song (From "Aaa")   
45                                   All Day Jolly Day   
46                                            Hey Sala   
47                                      Adada Mazhaida   
48                                        Kaatrukullai   
49                      Oru Kan Jaadai (From "Anjaan")   
50                                            Venmegam   
51                                      Pengal Yendral   
52                               Seermevum Koovathiley   
53                                 Idhayathai Oru Nodi   
54                                    Lets Be Friends?   
55                                      Ammadi Aathadi   
56                                   Unnai Unnai Unnai   
57                 Lovvu Lovvu - From "Anbulla Ghilli'   
58                  Over'a Feel Pannuren (From "Hero")   
59                      Malto Kithapuleh (From "Hero")   
60                           Title Track (From "Hero")   
61                                 Poongatre Poongatre   
62                                   Oh Shala Oh Shala   
63                                      Nenjai Kasakki   
64                                      Pachchai Vanna   
65                                   Suthudhe Suthudhe   
66                                  Kannan Varum Velai   
67                                    Kadal Raasa Naan   
68                                       E

In [ ]:
music_df.to_csv('music_data')

In [ ]:
# Function to calculate weighted popularity scores based on release date
def calculate_weighted_popularity(release_date):
    # Convert the release date to datetime object
    release_date = datetime.strptime(release_date, '%Y-%m-%d')

    # Calculate the time span between release date and today's date
    time_span = datetime.now() - release_date

    # Calculate the weighted popularity score based on time span (e.g., more recent releases have higher weight)
    weight = 1 / (time_span.days + 1)
    return weight

In [ ]:
# Normalize the music features using Min-Max scaling
scaler = MinMaxScaler()
music_features = music_df[['Danceability', 'Energy', 'Key',
                           'Loudness', 'Mode', 'Speechiness', 'Acousticness',
                           'Instrumentalness', 'Liveness', 'Valence', 'Tempo']].values
music_features_scaled = scaler.fit_transform(music_features)

In [ ]:
#a function to get content-based recommendations based on music features
def content_based_recommendations(input_song_name, num_recommendations=5):
    if input_song_name not in music_df['Track Name'].values:
        print(f"'{input_song_name}' not found in the dataset. Please enter a valid song name.")
        return

    # Get the index of the input song in the music DataFrame
    input_song_index = music_df[music_df['Track Name'] == input_song_name].index[0]

    # Calculate the similarity scores based on music features (cosine similarity)
    similarity_scores = cosine_similarity([music_features_scaled[input_song_index]], music_features_scaled)

    # Get the indices of the most similar songs
    similar_song_indices = similarity_scores.argsort()[0][::-1][1:num_recommendations + 1]

    # Get the names of the most similar songs based on content-based filtering
    content_based_recommendations = music_df.iloc[similar_song_indices][['Track Name', 'Artists', 'Album Name', 'Release Date', 'Popularity']]

    return content_based_recommendations

In [ ]:
def hybrid_recommendations(input_song_name, num_recommendations=5, alpha=0.5):
    if input_song_name not in music_df['Track Name'].values:
        print(f"'{input_song_name}' not found in the dataset. Please enter a valid song name.")
        return

    # Get content-based recommendations
    content_based_rec = content_based_recommendations(input_song_name, num_recommendations)

    # Get the popularity score of the input song
    popularity_score = music_df.loc[music_df['Track Name'] == input_song_name, 'Popularity'].values[0]

    # Calculate the weighted popularity score
    weighted_popularity_score = popularity_score * calculate_weighted_popularity(music_df.loc[music_df['Track Name'] == input_song_name, 'Release Date'].values[0])

    # Create a list to store the hybrid recommendations
    hybrid_recommendations = []

    # Append content-based recommendations to hybrid recommendations
    hybrid_recommendations.extend(content_based_rec.to_dict('records'))

    # Append input song with its weighted popularity score
    input_song_data = {
        'Track Name': input_song_name,
        'Artists': music_df.loc[music_df['Track Name'] == input_song_name, 'Artists'].values[0],
        'Album Name': music_df.loc[music_df['Track Name'] == input_song_name, 'Album Name'].values[0],
        'Release Date': music_df.loc[music_df['Track Name'] == input_song_name, 'Release Date'].values[0],
        'Popularity': weighted_popularity_score
    }
    hybrid_recommendations.append(input_song_data)

    # Convert the list of dictionaries to a DataFrame
    hybrid_recommendations_df = pd.DataFrame(hybrid_recommendations)

    # Sort the hybrid recommendations based on weighted popularity score
    hybrid_recommendations_df = hybrid_recommendations_df.sort_values(by='Popularity', ascending=False)

    # Remove the input song from the recommendations
    hybrid_recommendations_df = hybrid_recommendations_df[hybrid_recommendations_df['Track Name'] != input_song_name]

    return hybrid_recommendations_df


In [60]:
input_song_name = "Vallava Ennai"
recommendations = hybrid_recommendations(input_song_name, num_recommendations=5)
print(f"Hybrid recommended songs for '{input_song_name}':")
print(recommendations)

Hybrid recommended songs for 'Vallava Ennai':
                       Track Name  \
1                    High on Love   
0                       Poi Solla   
3                  Oru Kan Jaadai   
4  Oru Kan Jaadai (From "Anjaan")   
2                    High On Love   

                                          Artists  \
1                  Sid Sriram, Yuvan Shankar Raja   
0              Yuvan Shankar Raja, Sadhana Sargam   
3  Yuvan Shankar Raja, Benny Dayal, Shweta Pandit   
4  Yuvan Shankar Raja, Benny Dayal, Shweta Pandit   
2                   Yuvan Shankar Raja,Sid Sriram   

                                          Album Name Release Date  Popularity  
1  Pyaar Prema Kaadhal (Original Motion Picture S...   2018-02-13        64.0  
0  April Madhathil (Original Motion Picture Sound...   2002-11-10        48.0  
3        Anjaan (Original Motion Picture Soundtrack)   2014-07-25        45.0  
4                  All About Love: Yuvanshankar Raja   2018-08-31        36.0  
2  High On L

In [ ]:
pip install powerbiclient

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 684.9/684.9 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.2/102.2 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.0/317.0 MB 2.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 63.8 MB/s eta 0:00:00
  Created wheel for pyspark: filename=pyspark-3.5.1-py2.py3-none-any.whl size=317488491 sha256=a030ed2dba29ef675849fcd33ee8ae3a9364df64f3e2d682345f6efa6b860b4c
  Stored in directory: /root/.cache/pip/wheels/80/1d/60/2c256ed38dddce2fdd93be545214a63e02fbd8d74fb0b7f3a6
Successfully built pyspark


In [ ]:
from google.colab import output
output.enable_custom_widget_manager()

In [ ]:
from powerbiclient import QuickVisualize,get_dataset_config, Report,models
from powerbiclient.authentication import DeviceCodeLoginAuthentication
from powerbiclient.authentication import InteractiveLoginAuthentication
import pandas as pd

In [ ]:
auth=DeviceCodeLoginAuthentication()

Performing device flow authentication. Please follow the instructions below.
To sign in, use a web browser to open the page https://microsoft.com/devicelogin and enter the code EJT4XU5LW to authenticate.

Device flow authentication successfully completed.
You are now logged in .

The result should be passed only to trusted code in your notebook.


In [ ]:
PBI_Visualize = QuickVisualize(get_dataset_config(recommendations),auth=auth)
PBI_Visualize

QuickVisualize()

In [ ]:
from IPython.display import HTML

# Paste the HTML provided by Power BI here
power_bi_report_html = """
<iframe title="Music_Dashboard" width="1140" height="541.25" src="https://app.powerbi.com/reportEmbed?reportId=40ba9534-d5db-4608-a919-c73e8b380dad&autoAuth=true&ctid=d4963ce2-af94-4122-95a9-644e8b01624d" frameborder="0" allowFullScreen="true"></iframe>"""

# Display the HTML in the Jupyter Notebook
HTML(power_bi_report_html)


In [ ]:
# Set the display option to show all rows
pd.set_option('display.max_rows', None)

# Assuming 'df' is your DataFrame containing the dataset
# Display the entire DataFrame
display(music_df)


Track Name  \
0                      Yaaro Ivan (From "Udhayam NH4")   
1           Ae Le Le Etti Paarthale - From "Naiyaandi"   
2                              Vizhigalil Oru Vaanavil   
3                                      Yedhedho Pennae   
4                                          Kan Irandil   
5                                        Sotta Sotta m   
6                                          Kattu Kattu   
7                                       Kaadhal Endral   
8                                              Pogadhe   
9                             Idhayam (From "Billa 2")   
10                                        Iragai Poley   
11                                   Yedho Ondru Ennai   
12                                      Manmadhane Nee   
13                Aathadi Manasudhan (From "Kazhugoo")   
14                                          Oru Naalil   
15                                             Oh Baby   
16                                     En Kadhal Solla   
17                                  Evan Di Una Pethan   
18                                         Nallamdhana   
19                                        Nahna Na Nah   
20                            Mutham Kodutha Maayakari   
21                                       Vallava Ennai   
22                                        High On Love   
23                                            Neethane   
24                                      Kaadhal Vaithu   
25                                        Kannai Vittu   
26                                           Siragugal   
27                                Theeratha Vilaiyattu   
28                              Andha Kanna Paathaakaa   
29                                          Top Tucker   
30         Per Vachaalum Vaikkaama (From "Dikkiloona")   
31                                      Kambathu Ponnu   
32                                 Wake Me up Everyday   
33                    Thattiputta - From "Maamanithan"   
34                                        Kanave Urave   
35                                     Adi Yendi Pulla   
36                                         Thuli Thuli   
37                                    En Jannal Vandha   
38                                        Oru Devathai   
39                                   Saayndhu Saayndhu   
40                                   Chinna Chinnathai   
41                                      Enkeyoo Partha   
42                                              Vaanam   
43                                                 Goa   
44                             Trend Song (From "Aaa")   
45                                   All Day Jolly Day   
46                                            Hey Sala   
47                                      Adada Mazhaida   
48                                        Kaatrukullai   
49                      Oru Kan Jaadai (From "Anjaan")   
50                                            Venmegam   
51                                      Pengal Yendral   
52                               Seermevum Koovathiley   
53                                 Idhayathai Oru Nodi   
54                                    Lets Be Friends?   
55                                      Ammadi Aathadi   
56                                   Unnai Unnai Unnai   
57                 Lovvu Lovvu - From "Anbulla Ghilli'   
58                  Over'a Feel Pannuren (From "Hero")   
59                      Malto Kithapuleh (From "Hero")   
60                           Title Track (From "Hero")   
61                                 Poongatre Poongatre   
62                                   Oh Shala Oh Shala   
63                                      Nenjai Kasakki   
64                                      Pachchai Vanna   
65                                   Suthudhe Suthudhe   
66                                  Kannan Varum Velai   
67                                    Kadal Raasa Naan   
68                                       E

In [ ]:
# Reset the index to ensure consecutive numbering
music_df.reset_index(drop=True, inplace=True)
pd.set_option('display.max_rows', None)

# Assuming 'df' is your DataFrame containing the dataset
# Display the entire DataFrame
display(music_df)

Track Name  \
0                      Yaaro Ivan (From "Udhayam NH4")   
1           Ae Le Le Etti Paarthale - From "Naiyaandi"   
2                              Vizhigalil Oru Vaanavil   
3                                      Yedhedho Pennae   
4                                          Kan Irandil   
5                                        Sotta Sotta m   
6                                          Kattu Kattu   
7                                       Kaadhal Endral   
8                                              Pogadhe   
9                             Idhayam (From "Billa 2")   
10                                        Iragai Poley   
11                                   Yedho Ondru Ennai   
12                                      Manmadhane Nee   
13                Aathadi Manasudhan (From "Kazhugoo")   
14                                          Oru Naalil   
15                                             Oh Baby   
16                                     En Kadhal Solla   
17                                  Evan Di Una Pethan   
18                                         Nallamdhana   
19                                        Nahna Na Nah   
20                            Mutham Kodutha Maayakari   
21                                       Vallava Ennai   
22                                        High On Love   
23                                            Neethane   
24                                      Kaadhal Vaithu   
25                                        Kannai Vittu   
26                                           Siragugal   
27                                Theeratha Vilaiyattu   
28                              Andha Kanna Paathaakaa   
29                                          Top Tucker   
30         Per Vachaalum Vaikkaama (From "Dikkiloona")   
31                                      Kambathu Ponnu   
32                                 Wake Me up Everyday   
33                    Thattiputta - From "Maamanithan"   
34                                        Kanave Urave   
35                                     Adi Yendi Pulla   
36                                         Thuli Thuli   
37                                    En Jannal Vandha   
38                                        Oru Devathai   
39                                   Saayndhu Saayndhu   
40                                   Chinna Chinnathai   
41                                      Enkeyoo Partha   
42                                              Vaanam   
43                                                 Goa   
44                             Trend Song (From "Aaa")   
45                                   All Day Jolly Day   
46                                            Hey Sala   
47                                      Adada Mazhaida   
48                                        Kaatrukullai   
49                      Oru Kan Jaadai (From "Anjaan")   
50                                            Venmegam   
51                                      Pengal Yendral   
52                               Seermevum Koovathiley   
53                                 Idhayathai Oru Nodi   
54                                    Lets Be Friends?   
55                                      Ammadi Aathadi   
56                                   Unnai Unnai Unnai   
57                 Lovvu Lovvu - From "Anbulla Ghilli'   
58                  Over'a Feel Pannuren (From "Hero")   
59                      Malto Kithapuleh (From "Hero")   
60                           Title Track (From "Hero")   
61                                 Poongatre Poongatre   
62                                   Oh Shala Oh Shala   
63                                      Nenjai Kasakki   
64                                      Pachchai Vanna   
65                                   Suthudhe Suthudhe   
66                                  Kannan Varum Velai   
67                                    Kadal Raasa Naan   
68                                       E

In [ ]:
# Write the modified DataFrame to a CSV file with the index
music_df.to_csv('modified_music_data.csv')
